## 04_Xarray: Overlays from a cloud-served ERA5 archive

## Overview
1. Work with a cloud-served ERA5 archive
2. Subset the Dataset along its dimensions
3. Perform unit conversions
4. Create a well-labeled multi-parameter contour plot of gridded ERA5 data

## Imports

In [ ]:
import xarray as xr
import pandas as pd
import numpy as np
from datetime import datetime as dt
from metpy.units import units
import metpy.calc as mpcalc
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import matplotlib.pyplot as plt

## Select the region, time, and (if applicable) vertical level(s) of interest.

In [ ]:
# Areal extent

lonW = -100
lonE = -60
latS = 25
latN = 55
cLat, cLon = (latS + latN)/2, (lonW + lonE)/2

# Recall that in ERA5, longitudes run between 0 and 360, not -180 and 180
if (lonW < 0 ):
    lonW = lonW + 360
if (lonE < 0 ):
    lonE = lonE + 360
    
expand = 1
latRange = np.arange(latS - expand,latN + expand,.25) # expand the data range a bit beyond the plot range
lonRange = np.arange((lonW - expand),(lonE + expand),.25) # Need to match longitude values to those of the coordinate variable

# Vertical level specificaton
plevel = 500
levelStr = str(plevel)

# Date/Time specification
Year = 1998
Month = 5
Day = 31
Hour = 18
Minute = 0
dateTime = dt(Year,Month,Day, Hour, Minute)
timeStr = dateTime.strftime("%Y-%m-%d %H%M UTC")

## Work with a cloud-served ERA5 archive

A team at [Google Research & Cloud](https://research.google/) are making parts of the [ECMWF Reanalysis version 5](https://www.ecmwf.int/en/forecasts/dataset/ecmwf-reanalysis-v5) (aka **ERA-5**) accessible in a [Analysis Ready, Cloud Optimized](https://www.frontiersin.org/articles/10.3389/fclim.2021.782909/full) (aka **ARCO**) format.

Access the [ERA-5 ARCO](https://weatherbench2.readthedocs.io/en/latest/) catalog

The ERA5 archive runs from 1/1/1959 through 1/10/2023. For dates subsequent to the end-date, we'll instead load a local archive.

### If the requested date is later than 1/10/2023, read in the dataset from a locally-stored archive.

In [ ]:
endDate = dt(2023,1,10)
if (dateTime <= endDate):

    cloud_source = True
    ds = xr.open_dataset(
     'gs://weatherbench2/datasets/era5/1959-2023_01_10-wb13-6h-1440x721.zarr', 
     chunks={'time': 48},
     consolidated=True,
     engine='zarr'
)

else: 
    import glob, os
    cloud_source = False
    input_directory = '/free/ktyle/era5'
    files = glob.glob(os.path.join(input_directory,'*.nc'))
    ds = xr.open_mfdataset(files)

print(f'size: {ds.nbytes / (1024 ** 4)} TB')

The cloud-hosted dataset is a **big** (40+ TB) file! But Xarray is just reading only enough of the file for us to get a look at the dimensions, coordinate and data variables, and other metadata. We call this *lazy loading*, as opposed to *eager loading*, which we will do only after we have subset the dataset over time, lat-lon, and vertical level.

### Examine the dataset

In [ ]:
ds

<div class="alert alert-warning"><b>Pay attention to the names of the data and coordinate variables!</b> The locally-stored dataset differs from the cloud-served one in all but <i>latitude</i> and <i>longtiude</i>.
</div>

### Data variables selection and subsetting
We'll retrieve two data variables (i.e. `DataArray`s), geopotential and sea-level pressure, from the `Dataset`.

In [ ]:
if (cloud_source):
    z = ds['geopotential'].sel(time=dateTime,level=plevel,latitude=latRange,longitude=lonRange)
    slp = ds['mean_sea_level_pressure'].sel(time=dateTime,latitude=latRange,longitude=lonRange)
else:
    z = ds['z'].sel(valid_time=dateTime,pressure_level=plevel,latitude=latRange,longitude=lonRange)
    slp = ds['msl'].sel(valid_time=dateTime,latitude=latRange,longitude=lonRange) 

#### Define our subsetted coordinate arrays of lat and lon. Pull them from either of the two DataArrays. We'll need to pass these into the contouring functions later on.

In [ ]:
lats = z.latitude
lons = z.longitude

## Perform unit conversions

Convert geopotential in `m**2/s**2` to geopotential height in decameters (`dam`), and Pascals to hectoPascals (`hPa`).

We take the DataArrays and apply [MetPy's unit conversion methods](https://unidata.github.io/MetPy/latest/tutorials/xarray_tutorial.html#units).

In [ ]:
slp = slp.metpy.convert_units('hPa')
z = mpcalc.geopotential_to_height(z).metpy.convert_units('dam')

<div class="alert alert-warning">These conversions involve actual calculations, so in that cell, we are not *lazy-loading*. But that is the first instance where actual bytes of anything other than metadata get transfered ... <i>and we've already subset our original much larger datsets into something much smaller</i>.
</div>

In [ ]:
slp.nbytes / 1e6, z.nbytes / 1e6 # size in MB for the subsetted DataArrays

In [ ]:
z

## Create a well-labeled multi-parameter contour plot of gridded ERA5 reanalysis data

We will make contour fills of 500 hPa height in decameters, with a contour interval of 6 dam, and contour lines of SLP in hPa, contour interval = 4.

As we've done before, let's first define some variables relevant to Cartopy. Recall that we already defined the areal extent up above when we did the data subsetting.

In [ ]:
proj_map = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)
proj_data = ccrs.PlateCarree() # Our data is lat-lon; thus its native projection is Plate Carree.
res = '50m'

#### Now define the range of our contour values and a contour interval. 60 m is standard for 500 hPa.

In [ ]:
minVal = 474
maxVal = 606
cint = 6
Zcintervals = np.arange(minVal, maxVal, cint)
Zcintervals

In [ ]:
minVal = 900
maxVal = 1080
cint = 4
SLPcintervals = np.arange(minVal, maxVal, cint)
SLPcintervals

### Plot the map, with filled contours of 500 hPa geopotential heights, and contour lines of SLP.

Create a meaningful title string.

In [ ]:
tl1 = f"ERA5 {levelStr} hPa heights (dam, filled contours) and SLP (lines, hPa)"
tl2 = f"Valid at: {timeStr}"
title_line = (tl1 + '\n' + tl2 + '\n')

In [ ]:
proj_map = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)
proj_data = ccrs.PlateCarree()
res = '50m'
fig = plt.figure(figsize=(18,12))
ax = plt.subplot(1,1,1,projection=proj_map)
ax.set_extent ([lonW,lonE,latS,latN])
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature(cfeature.STATES.with_scale(res))
CF = ax.contourf(lons,lats,z, levels=Zcintervals,transform=proj_data,cmap=plt.get_cmap('coolwarm'))
cbar = plt.colorbar(CF,shrink=0.5)
cbar.ax.tick_params(labelsize=16)
cbar.ax.set_ylabel("Height (dam)",fontsize=16)

CL = ax.contour(lons,lats,slp,SLPcintervals,transform=proj_data,linewidths=1.25,colors='green')
ax.clabel(CL, inline_spacing=0.2, fontsize=11, fmt='%.0f')
title = plt.title(title_line,fontsize=16)

### Constrain the map plotting region to eliminate blank space on the east & west edges of the domain.

In [ ]:
constrainLon = 7 # trial and error!

proj_map = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)
proj_data = ccrs.PlateCarree()
res = '50m'
fig = plt.figure(figsize=(18,12))
ax = plt.subplot(1,1,1,projection=proj_map)
ax.set_extent ([lonW+constrainLon,lonE-constrainLon,latS,latN])
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature(cfeature.STATES.with_scale(res))
CF = ax.contourf(lons,lats,z,levels=Zcintervals,transform=proj_data,cmap=plt.get_cmap('coolwarm'))
cbar = plt.colorbar(CF,shrink=0.5)
cbar.ax.tick_params(labelsize=16)
cbar.ax.set_ylabel("Height (dam)",fontsize=16)

CL = ax.contour(lons,lats,slp,SLPcintervals,transform=proj_data,linewidths=1.25,colors='green')
ax.clabel(CL, inline_spacing=0.2, fontsize=11, fmt='%.0f')
title = plt.title(title_line,fontsize=16)

## Things to try:
1. Change the date and time
2. Change the region
3. Use a different map projection for your plot
4. Select and overlay different variables